In [3]:
!cd DI725_Final_Project/src/

In [1]:
import pandas as pd
from torch.utils.data import Dataset, DataLoader
from transformers import AutoProcessor, PaliGemmaForConditionalGeneration
from PIL import Image
import torch
from tqdm import tqdm

In [2]:
from google.colab import drive
drive.mount('/content/drive')

Mounted at /content/drive


In [3]:
# === Configuration ===
CSV_PATH = "DI725_Final_Project/data/RISCM/captions.csv"
IMAGE_DIR = "/content/drive/MyDrive/data/RISCM/resized/"
MODEL_ID = "google/paligemma-3b-mix-224"
DEVICE = "cuda" if torch.cuda.is_available() else "cpu"
DTYPE = torch.bfloat16 if torch.cuda.is_available() else torch.float32

In [4]:
# === Load CSV ===
df = pd.read_csv(CSV_PATH)
train_df = df[df['split'] == 'train'].reset_index(drop=True)
val_df = df[df['split'] == 'val'].reset_index(drop=True)

In [5]:
!huggingface-cli login


    _|    _|  _|    _|    _|_|_|    _|_|_|  _|_|_|  _|      _|    _|_|_|      _|_|_|_|    _|_|      _|_|_|  _|_|_|_|
    _|    _|  _|    _|  _|        _|          _|    _|_|    _|  _|            _|        _|    _|  _|        _|
    _|_|_|_|  _|    _|  _|  _|_|  _|  _|_|    _|    _|  _|  _|  _|  _|_|      _|_|_|    _|_|_|_|  _|        _|_|_|
    _|    _|  _|    _|  _|    _|  _|    _|    _|    _|    _|_|  _|    _|      _|        _|    _|  _|        _|
    _|    _|    _|_|      _|_|_|    _|_|_|  _|_|_|  _|      _|    _|_|_|      _|        _|    _|    _|_|_|  _|_|_|_|

    To log in, `huggingface_hub` requires a token generated from https://huggingface.co/settings/tokens .
Enter your token (input will not be visible): 
Add token as git credential? (Y/n) y
Token is valid (permission: fineGrained).
The token `hf-token` has been saved to /root/.cache/huggingface/stored_tokens
Cannot authenticate through git-credential as no helper is defined on your machine.
You might have to re-authenticate

In [6]:
# === Load Model and Processor ===
model = PaliGemmaForConditionalGeneration.from_pretrained(
    MODEL_ID,
    torch_dtype=DTYPE,
    device_map="cuda:0"
).to(DEVICE)
model.gradient_checkpointing_enable()
model.train()

processor = AutoProcessor.from_pretrained(MODEL_ID)

/usr/local/lib/python3.11/dist-packages/huggingface_hub/utils/_auth.py:94: UserWarning: 
The secret `HF_TOKEN` does not exist in your Colab secrets.
To authenticate with the Hugging Face Hub, create a token in your settings tab (https://huggingface.co/settings/tokens), set it as secret in your Google Colab and restart your session.
You will be able to reuse this secret in all of your notebooks.
Please note that authentication is recommended but still optional to access public models or datasets.
  warnings.warn(


config.json:   0%|          | 0.00/1.03k [00:00<?, ?B/s]

model.safetensors.index.json:   0%|          | 0.00/62.6k [00:00<?, ?B/s]

Fetching 3 files:   0%|          | 0/3 [00:00<?, ?it/s]

model-00003-of-00003.safetensors:   0%|          | 0.00/1.74G [00:00<?, ?B/s]

...

tokenizer_config.json:   0%|          | 0.00/40.0k [00:00<?, ?B/s]

tokenizer.model:   0%|          | 0.00/4.26M [00:00<?, ?B/s]

tokenizer.json:   0%|          | 0.00/17.5M [00:00<?, ?B/s]

added_tokens.json:   0%|          | 0.00/24.0 [00:00<?, ?B/s]

special_tokens_map.json:   0%|          | 0.00/607 [00:00<?, ?B/s]

In [7]:
# === Dataset Class ===
class CaptionDataset(Dataset):
    def __init__(self, dataframe, processor, image_dir):
        self.df = dataframe
        self.processor = processor
        self.image_dir = image_dir

    def __len__(self):
        return len(self.df)

    def __getitem__(self, idx):
        row = self.df.iloc[idx]
        image_path = self.image_dir + row['image']
        caption = row['caption_1']
        image = Image.open(image_path).convert("RGB")

        prompt = "<image> " + processor.tokenizer.bos_token + " caption en"
        model_inputs = self.processor(
            text=prompt,
            images=image,
            suffix=caption,
            return_tensors="pt",
            padding="max_length",
            truncation=True,
            max_length=64,
            add_special_tokens=False
        )
        input_ids = model_inputs["input_ids"].squeeze(0)
        attention_mask = model_inputs["attention_mask"].squeeze(0)
        pixel_values = model_inputs["pixel_values"].squeeze(0)

        labels = self.processor(
            text=caption,
            images=image,
            return_tensors="pt",
            padding="max_length",
            max_length=64,
            truncation=True
        )["input_ids"].squeeze(0)

        return {
            "input_ids": input_ids,
            "attention_mask": attention_mask,
            "pixel_values": pixel_values,
            "labels": labels,
            "text": caption
        }

In [8]:
# === DataLoader ===
train_dataset = CaptionDataset(train_df, processor, IMAGE_DIR)
val_dataset = CaptionDataset(val_df, processor, IMAGE_DIR)
train_loader = DataLoader(train_dataset, batch_size=1, shuffle=True)
val_loader = DataLoader(val_dataset, batch_size=1, shuffle=False)

# === Optimizer ===
optimizer = torch.optim.AdamW(model.parameters(), lr=5e-5)

In [9]:
import os
os.environ["PYTORCH_CUDA_ALLOC_CONF"] = "expandable_segments:True"

In [ ]:
# === Training Loop ===
for epoch in range(3):
    total_loss = 0
    model.train()
    for batch in tqdm(train_loader, desc=f"Epoch {epoch + 1} - Training"):
        optimizer.zero_grad()
        with torch.amp.autocast(device_type='cuda', dtype=torch.bfloat16):
            outputs = model(
                input_ids=batch['input_ids'].to(DEVICE),
                attention_mask=batch['attention_mask'].to(DEVICE),
                pixel_values=batch['pixel_values'].to(DEVICE),
                labels=batch['labels'].to(DEVICE)
            )
            loss = outputs.loss

        loss.backward()
        optimizer.step()
        torch.cuda.empty_cache()


        total_loss += loss.item()

    avg_train_loss = total_loss / len(train_loader)
    print(f"Epoch {epoch + 1} | Avg Train Loss: {avg_train_loss:.4f}")

Streaming output truncated to the last 5000 lines.
Epoch 1 - Training: 100%|██████████| 35614/35614 [6:28:29<00:00,  1.53it/s]


Epoch 1 | Avg Train Loss: 0.0436


Streaming output truncated to the last 5000 lines.
Epoch 2 - Training:  66%|██████▌   | 23442/35614 [2:16:38<1:10:49,  2.86it/s]You are passing both `text` and `images` to `PaliGemmaProcessor`. The processor expects special image tokens in the text, as many tokens as there are images per each text. It is recommended to add `<image>` tokens in the very beginning of your text. For this call, we will infer how many images each text has and add special tokens.


In [ ]:
    # === Validation ===
    model.eval()
    val_loss = 0
    with torch.no_grad():
        for batch in tqdm(val_loader, desc=f"Epoch {epoch + 1} - Validation"):
            with torch.cuda.amp.autocast(dtype=torch.bfloat16):
                outputs = model(
                    input_ids=batch['input_ids'].to(DEVICE),
                    attention_mask=batch['attention_mask'].to(DEVICE),
                    pixel_values=batch['pixel_values'].to(DEVICE),
                    labels=batch['labels'].to(DEVICE)
                )
                val_loss += outputs.loss.item()

    avg_val_loss = val_loss / len(val_loader)
    print(f"Epoch {epoch + 1} | Avg Val Loss: {avg_val_loss:.4f}")

In [ ]:
# === Save Final Model ===
model.save_pretrained("/content/drive/MyDrive/paligemma-finetuned")
processor.save_pretrained("/content/drive/MyDrive/paligemma-finetuned")